This is my Fantasy Hockey Analyzer. The purpose of this project is to predict the fantasy hockey output of individual skaters based on stats from previous years.


Section 1: Modules Used

The following is a list of modules that I used and the reason why they were used:

-os: to allow the program to read data in the repository

-numpy: basic math operations

-pandas: all dataframe operations/data storage/data cleaning

-various sklearn: all machine learning operations/analysis

In addition to these modules, I also have a custom module that contains helper functions that help in data cleaning/accuracy evaluation. These functions are contained in the "my_module.py" file in the repository. If you are interested in taking a look at these functions, they are available at https://github.com/chrisberry888/FantasyHockeyAnalyzer in the "my_module.py" file.

In [1]:
#Import block
import os
import numpy as np
import pandas as pd
from sklearn.neural_network import MLPRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.datasets import make_regression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error

import my_module as mx

Section 2: Data Gathering and Cleaning

The ultimate goal of this project is to predict the number of fantasy points that a given player will have in the 2022-2023 season. Different fantasy leagues have different points breakdowns, but my current league has a points breakdown as described in the "points_dict" variable in the following code block. For example, each player gets 5 fantasy points for a goal, 3 for an assist, and so on. Of course, this can be changed if a different league has a different points breakdown.

To accomplish this all, I have gathered data from rotowire.com and moneypuck.com. The Moneypuck data contains just about every advanced stat you could think of in a variety of different situations (5-on-5, 5-on-4, etc). However, for the sake of this project we will only use their data that describes a player's output in all of their situations. The only stat we need that can't be calculated using the Moneypuck data is +/-; Rotowire has +/- available, so I'm using that dataset.

Data from these sets start from the 2010-2011 season and stretch to the 2021-2022 season. All of the major data gathering and cleaning occurs in the next three code blocks.


The following block does all of the prep work before we start to read the data. It first establishes where the data is stored in the repository so that it can be read by the program. It then creates a list of labels that will be used by the rotowire data (the rotowire dataset is formatted differently than the moneypuck dataset, so we need to do this extra step before proceeding). It then establishes a points breakdown for each relevant stat; this is used later on to calculate fantasy points for each player.

In [2]:
#The current working directory is the main repository directory; these lines set the path to where the data is
path = os.getcwd()
data_path = path + '\\data'

#This array makes it easier to format the rotowire data
rw_labels = ["name", "Team", "Pos", "Games", "Goals", "Assists", "Pts", "+/-", "PIM", "SOG", "GWG", "PP_Goals", "PP_Assists", "SH_Goals", "SH_Assists", "Hits", "Blocked_Shots"]

#This is the breakdown of how many fantasy points a player gets for each category
points_dict = {"Goals":5, "Assists":3, "+/-":1.5, "PIM":-0.25, "PP_Goals":4, "PP_Assists":2, "SH_Goals":6, "SH_Assists":4, "Faceoffs_Won":0.25, "Faceoffs_Lost":-0.15, "Hits":0.5, "Blocked_Shots":0.75 }


The following block takes all of the data in the repository and turns it into year-by-year player data. For each year from 2010 to 2021, the for-loop reads the rotowire and moneypuck data from the csv files in the repository, merges the datasets together, calculates the player's fantasy points for that season, does some formatting, then adds it to the "yearly_player_data" list. This list can be used later on for turning into ML-readable data.

In [3]:
#I have data from the 2010-2011 season through the 2021-2022 season.
#By the end of this block, there will be 12 seasons-worth of data in the "data" variable
yearly_player_data = []

for i in range(2010, 2022):
    new_data = []
    
    #Imports the rotowire and moneypuck datasets from the selected year into rdf and mdf
    rdf = pd.read_csv(data_path + '\\rotowire_data\\rotowire{}.csv'.format(str(i)))
    mdf = pd.read_csv(data_path + '\\moneypuck_data\\moneypuck{}.csv'.format(str(i)))
    
    #Formats the rotowire data
    rdf.set_axis(rw_labels, axis=1, inplace=True)
    rdf.drop(index=rdf.index[0], axis=0, inplace=True)
    
    #The Moneypuck data has information about 5-on-5, 5-on-4, 4-on-5, other, and all.
    #For this project I'm just focused on "all" since I suspect it'll give me the best results.
    mdf = mdf[mdf["situation"] == "all"]
    
    #Combines the "Name" and "Team" columns (There are some players with the same name on different teams)
    rdf["name"] = rdf["name"] + "-" + rdf["Team"]
    mdf["name"] = mdf["name"] + "-" + mdf["team"]
    
    
    
    #Merges the rotowire and moneypuck dataframes
    new_data = pd.merge(rdf, mdf, on="name")
    
    #Changes the name of a few columns in the new dataframe
    new_data = new_data.rename(columns={"name":"Name","faceoffsWon":"Faceoffs_Won","faceoffsLost":"Faceoffs_Lost"})
    
    #This section calculates each player's total fantasy output for that year
    cols = new_data.columns
    fant_points = [0 for i in range(len(new_data))]
    for i in range(len(new_data)):
        for j in range(len(new_data.iloc[i])):
            mult = points_dict.get(cols[j], 0)
            if mult != 0:
                fant_points[i] += mult*int(new_data.iloc[i, j])
    
    #Adds the players' fantasy points to the new_data dataframe
    new_data["Fantasy_Points"] = fant_points
    
    new_data = new_data.drop_duplicates()
    
    #Adds new_data to the "data" array
    yearly_player_data.append(new_data)
                
    



In [4]:
pd.options.display.max_columns = None
pd.options.display.max_rows = None
yearly_player_data[11]

Name Team Pos Games Goals Assists  Pts  +/-  PIM  \
0           Elias Lindholm-CGY  CGY  RW    82    42      40   82   61   22   
1              Devon Toews-COL  COL   D    66    13      44   57   52   20   
2               Cale Makar-COL  COL   D    77    28      58   86   48   26   
3             Justin Faulk-STL  STL   D    76    16      31   47   41   43   
4          Gustav Forsling-FLA  FLA   D    71    10      27   37   41   18   
5           Alex Goligoski-MIN  MIN   D    72     2      28   30   41   34   
6             Aaron Ekblad-FLA  FLA   D    61    15      42   57   38   26   
7        Aleksander Barkov-FLA  FLA   C    67    39      49   88   36   18   
8           Mikko Rantanen-COL  COL  RW    75    36      56   92   35   56   
9            Jaccob Slavin-CAR  CAR   D    79     4      38   42   35   10   
10        Oliver Kylington-CGY  CGY   D    73     9      22   31   34   14   
11           Anton Lundell-FLA  FLA   C    65    18      26   44   33   18   
12          Jared Spurgeon-MIN  MIN   D    65    10      30   40   32   10   
13            Ryan Hartman-MIN  MIN  RW    82    34      31   65   31   95   
14          Charlie McAvoy-BOS  BOS   D    78    10      46   56   31   66   
15          Mika Zibanejad-NYR  NYR   C    81    29      52   81   30   12   
16        Rasmus Andersson-CGY  CGY   D    82     4      46   50   30   28   
17        Pavel Buchnevich-STL  STL  LW    73    30      46   76   29   34   
18          Connor McDavid-EDM  EDM   C    80    44      79  123   28   45   
19         Kirill Kaprizov-MIN  MIN  LW    81    47      61  108   27   34   
20       Gabriel Landeskog-COL  COL  LW    51    30      29   59   27   78   
21             Sam Bennett-FLA  FLA  LW    71    28      21   49   27   74   
22         Michael Bunting-TOR  TOR  LW    79    23      40   63   27   80   
23            Noah Hanifin-CGY  CGY   D    81    10      38   48   27   19   
24             Radko Gudas-FLA  FLA   D    77     3      13   16   27  105   
25        Patrice Bergeron-BOS  BOS   C    73    25      40   65   26   32   
26         Jordan Greenway-MIN  MIN  LW    62    10      17   27   26   69   
27       Alexandre Carrier-NSH  NSH   D    77     3      27   30   26   50   
28            Sam Reinhart-FLA  FLA  RW    78    33      49   82   25   13   
29          Marcus Foligno-MIN  MIN  LW    74    23      19   42   25  112   
30            Evander Kane-EDM  EDM  LW    43    22      17   39   25   60   
31            Jacob Trouba-NYR  NYR   D    81    11      28   39   25   88   
32        Carter Verhaeghe-FLA  FLA   C    78    24      31   55   24   48   
33             Jesper Fast-CAR  CAR  RW    82    14      20   34   24    4   
34          Brian Dumoulin-PIT  PIT   D    76     3      15   18   24   24   
35              Torey Krug-STL  STL   D    64     9      34   43   23   48   
36          K'Andre Miller-NYR  NYR   D    82     7      13   20   23   24   
37        Nathan MacKinnon-COL  COL   C    65    32      56   88   22   42   
38        Teuvo Teravainen-CAR  CAR   C    77    22      43   65   22   24   
39        Jesse Puljujarvi-EDM  EDM  RW    65    14      22   36   22   20   
40             Brady Skjei-CAR  CAR   D    82     9      30   39   22   48   
41            Erik Johnson-COL  COL   D    77     8      17   25   22   24   
42           Matt Grzelcyk-BOS  BOS   D    73     4      20   24   22   24   
43       Valeri Nichushkin-COL  COL  LW    62    25      27   52   21   14   
44          Brayden Schenn-STL  STL   C    62    24      34   58   21   33   
45         Mats Zuccarello-MIN  MIN  RW    70    24      55   79   21   24   
46          Artemi Panarin-NYR  NYR  LW    75    22      74   96   21   18   
47         Zach Whitecloud-VGK  VGK   D    59     8      11   19   21   20   
48         Auston Matthews-TOR  TOR   C    73    60      46  106   20   18   
49       Andrew Mangiapane-CGY  CGY  LW    82    35      20   55   20   38   
50             Kris Letang-PIT  PIT   D    78   

The following block takes the yearly data and turns it into ML-readable data. For this project, I am creating different models that use data from the past one year, the past two years, and the past three years, and seeing how much they differ in terms of efficacy.

In [5]:
ml_data_one_year = pd.DataFrame()
ml_data_two_year = pd.DataFrame()
ml_data_three_year = pd.DataFrame()
for i in range(2011, 2022):
    arr = [yearly_player_data[i-2011]]
    points_df = yearly_player_data[i-2010]
    temp = mx.merge_dataframes(arr, points_df)
    ml_data_one_year = pd.concat([ml_data_one_year, temp], ignore_index=True)
    
for i in range(2012, 2022):
    arr = [yearly_player_data[i-2012], yearly_player_data[i-2011]]
    points_df = yearly_player_data[i-2010]
    temp = mx.merge_dataframes(arr, points_df)
    ml_data_two_year = pd.concat([ml_data_two_year, temp], ignore_index=True)
    
for i in range(2013, 2022):
    arr = [yearly_player_data[i-2013], yearly_player_data[i-2012], yearly_player_data[i-2011]]
    points_df = yearly_player_data[i-2010]
    temp = mx.merge_dataframes(arr, points_df)
    ml_data_three_year = pd.concat([ml_data_three_year, temp], ignore_index=True)



Section 3:

Now that we have the data that ml models can read, we can now train the models. For this project, I'm using multi-layer perceptrons (MLPRegressor) and Random Forests (RandomForestRegressor). I'm making six total models: a MLP each for the one- two- and three-year data, and a Random Forest each for the one- two- and three-year data.

ONE YEAR:

In [6]:
arr = mx.separate_fantasy_points(ml_data_one_year)
X = mx.reformat_df(arr[0])
y = arr[1]

X_train_one, X_test_one, y_train_one, y_test_one = train_test_split(X, y)

one_year_regr = MLPRegressor(max_iter=1000)
one_year_regr.fit(X_train_one, y_train_one)

one_year_RF = RandomForestRegressor()
one_year_RF.fit(X_train_one, y_train_one)



RandomForestRegressor()

TWO YEAR:

In [7]:
arr = mx.separate_fantasy_points(ml_data_two_year)
X = mx.reformat_df(arr[0])
y = arr[1]

X_train_two, X_test_two, y_train_two, y_test_two = train_test_split(X, y)

two_year_regr = MLPRegressor(max_iter=1000)
two_year_regr.fit(X_train_two, y_train_two)

two_year_RF = RandomForestRegressor()
two_year_RF.fit(X_train_two, y_train_two)



RandomForestRegressor()

THREE YEAR:

In [8]:
arr = mx.separate_fantasy_points(ml_data_three_year)
X = mx.reformat_df(arr[0])
y = arr[1]

X_train_three, X_test_three, y_train_three, y_test_three = train_test_split(X, y)

three_year_regr = MLPRegressor(max_iter=1000)
three_year_regr.fit(X_train_three, y_train_three)

three_year_RF = RandomForestRegressor()
three_year_RF.fit(X_train_three, y_train_three)



RandomForestRegressor()

Section 4: Analysis

Now that we have the models trained, we can analyze them. We'll be analyzing the data in two ways: first, we'll see how accurate the actual points predictions are using the mean_absolute_error.

In [9]:
y_pred = one_year_regr.predict(X_test_one)
print(mean_absolute_error(y_test_one, y_pred))

y_pred = two_year_regr.predict(X_test_two)
print(mean_absolute_error(y_test_two, y_pred))

y_pred = three_year_regr.predict(X_test_three)
print(mean_absolute_error(y_test_three, y_pred))

y_pred = one_year_RF.predict(X_test_one)
print(mean_absolute_error(y_test_one, y_pred))

y_pred = two_year_RF.predict(X_test_two)
print(mean_absolute_error(y_test_two, y_pred))

y_pred = three_year_RF.predict(X_test_three)
print(mean_absolute_error(y_test_three, y_pred))

83.40516968497543
83.9488374287591
74.22160201494788
78.47220397111913
78.18138402061855
80.01302877697843


The MAE for all of the models range between around 70 and around 95. Given that most players in the league finish with a fantasy point total in the hundreds, we can see that the predicted points values aren't very accurate to the real-life values. However, we are less concerned with the actual points total that a player will have, and more concerned with their rank within the rest of the league. To look at this, we will rank the players both in terms of predicted fantasy points for a season, and actual fantasy points for a season. (I'll incorporate this at a later time)

Section 5: Predictions for Next Year

Now that we've taken a look at the accuracy of the model, we'll see what the models think will happen in the 2022-2023 season. 

In [10]:
one_year_pred = yearly_player_data[11].copy()
one_year_pred.drop(columns=["Fantasy_Points"], inplace=True)
one_year_df = mx.get_name_predictions(one_year_regr, one_year_pred)
one_year_df.sort_values(by="Prediction", ascending=False, inplace=True)
#pd.options.display.max_rows = 978
display(one_year_df)


Name  Prediction
48         Auston Matthews-TOR  367.692412
25        Patrice Bergeron-BOS  339.990438
7        Aleksander Barkov-FLA  319.172022
37        Nathan MacKinnon-COL  303.619712
0           Elias Lindholm-CGY  302.652340
83          David Pastrnak-BOS  293.428187
56           Sebastian Aho-CAR  290.855385
18          Connor McDavid-EDM  288.357428
20       Gabriel Landeskog-COL  288.146526
405           John Tavares-TOR  285.435678
62          Leon Draisaitl-EDM  285.386218
154              Bo Horvat-VAN  285.273295
55       Andrei Svechnikov-CAR  282.554675
394            Josh Norris-OTT  281.948649
73             Roope Hintz-DAL  279.219036
74             J.T. Miller-VAN  279.047867
8           Mikko Rantanen-COL  273.813765
88          Filip Forsberg-NSH  271.796877
66           Brad Marchand-BOS  268.403820
395          Brady Tkachuk-OTT  268.126768
53           Sidney Crosby-PIT  267.001124
65         Jason Robertson-DAL  263.471552
67        Joel Eriksson Ek-MIN  262.597380
15          Mika Zibanejad-NYR  262.257585
373      Pierre-Luc Dubois-WPG  260.126071
57          Nikolaj Ehlers-WPG  259.482985
148        Drake Batherson-OTT  256.947516
82           Jake Guentzel-PIT  254.642176
28            Sam Reinhart-FLA  254.599586
19         Kirill Kaprizov-MIN  252.174873
43       Valeri Nichushkin-COL  251.320774
476          Tage Thompson-BUF  251.010208
39        Jesse Puljujarvi-EDM  249.099795
94            Joe Pavelski-DAL  247.473948
52           Chris Kreider-NYR  246.862438
418       William Nylander-TOR  244.836738
480           Dylan Larkin-DET  244.751303
501           Jared McCann-SEA  239.667484
30            Evander Kane-EDM  239.247270
99            Jordan Staal-CAR  239.229428
477         Mark Scheifele-WPG  238.333298
123     Vladimir Tarasenko-STL  238.298532
321            Kyle Connor-WPG  237.334866
13            Ryan Hartman-MIN  237.252311
2               Cale Makar-COL  237.195649
189       Elias Pettersson-VAN  235.912737
6             Aaron Ekblad-FLA  234.590542
124             Bryan Rust-PIT  234.466452
503            Tim Stutzle-OTT  233.772341
327          Thomas Chabot-OTT  233.329900
11           Anton Lundell-FLA  233.220411
132           Matt Duchene-NSH  233.084703
21             Sam Bennett-FLA  232.002661
158       William Karlsson-VGK  229.609696
63           Robert Thomas-STL  229.344438
323              Alex Tuch-BUF  228.311843
162         Miro Heiskanen-DAL  227.448532
60           Darnell Nurse-EDM  227.343068
419             Zach Hyman-EDM  227.335862
157            Jack Eichel-VGK  225.804253
490           Tyler Seguin-DAL  222.616199
160    Ryan Nugent-Hopkins-EDM  221.883373
440         Tyler Bertuzzi-DET  221.621287
406            Jeff Carter-PIT  220.620676
294          Ryan Johansen-NSH  220.286766
96           Ryan O'Reilly-STL  220.025107
149           Reilly Smith-VGK  219.613534
69         Mikael Backlund-CGY  219.565573
49       Andrew Mangiapane-CGY  218.736682
70           Morgan Rielly-TOR  218.328005
89             Nicolas Roy-VGK  218.030935
155  Jonathan Marchessault-VGK  217.615413
98             Seth Jarvis-CAR  216.711393
22         Michael Bunting-TOR  215.816871
359           Brock Boeser-VAN  212.603482
378         Sean Couturier-PHI  212.376317
84              Roman Josi-NSH  211.710780
45         Mats Zuccarello-MIN  211.451463
510             Seth Jones-CHI  207.224958
17        Pavel Buchnevich-STL  206.811812
423        Mikael Granlund-NSH  205.684205
140    Chandler Stephenson-VGK  203.978802
14          Charlie McAvoy-BOS  203.626443
106           Quinn Hughes-VAN  203.499340
117          Rasmus Sandin-TOR  203.246301
448           Yanni Gourde-SEA  202.367784
97             Taylor Hall-BOS  202.363242
223    Jean-Gabriel Pageau-NYI  201.538380
408         Barrett Hayton-ARI  201.451505
38        Teuvo Teravainen-CAR  200.346835
1              Devon Toews-COL  199.879821
458           Jeff Skinner-BUF  199.454750
433          Evgeni Malkin-

In [11]:
two_year_pred = [yearly_player_data[i] for i in [10,11]]
two_year_pred = mx.merge_dataframes(two_year_pred, yearly_player_data[11])
two_year_pred.drop(columns=["Predicted_Fantasy_Points"], inplace=True)
two_year_df = mx.get_name_predictions(two_year_regr, two_year_pred)
two_year_df.sort_values(by="Prediction", ascending=False, inplace=True)
#pd.options.display.max_rows = 978
display(two_year_df)

Name  Prediction
0          Auston Matthews-TOR  411.503742
7        Aleksander Barkov-FLA  379.141166
2           Leon Draisaitl-EDM  374.008336
1           Connor McDavid-EDM  371.924000
15        Patrice Bergeron-BOS  368.813778
21        Nathan MacKinnon-COL  368.149010
3           Mikko Rantanen-COL  355.664922
214           Tyler Seguin-DAL  344.002712
26          Elias Lindholm-CGY  339.576997
55             Roope Hintz-DAL  330.012268
11          Mika Zibanejad-NYR  329.962365
9            Sidney Crosby-PIT  329.306057
98       Pierre-Luc Dubois-WPG  327.376337
51             J.T. Miller-VAN  322.976108
12           Sebastian Aho-CAR  318.192873
25            John Tavares-TOR  318.176838
45           Darnell Nurse-EDM  317.264194
22       Gabriel Landeskog-COL  313.025224
95        Elias Pettersson-VAN  311.399515
138           Matt Duchene-NSH  311.386244
5          Kirill Kaprizov-MIN  309.810950
113             Cale Makar-COL  308.642001
14           Jake Guentzel-PIT  306.437889
8             Joe Pavelski-DAL  304.481123
27               Bo Horvat-VAN  304.169529
4            Brad Marchand-BOS  303.288113
150         Charlie McAvoy-BOS  301.637440
36           Brady Tkachuk-OTT  300.858358
88       Valeri Nichushkin-COL  300.088422
282      Timothy Liljegren-TOR  299.609495
6              Kyle Connor-WPG  296.941127
23           Chris Kreider-NYR  296.076593
10           Ryan O'Reilly-STL  294.790211
123            Kris Letang-PIT  293.589186
110             Roman Josi-NSH  293.355622
20          David Pastrnak-BOS  292.304015
160       Rasmus Andersson-CGY  291.923101
104            Devon Toews-COL  291.068435
114          Tage Thompson-BUF  290.939673
16              Bryan Rust-PIT  289.456893
37             Josh Norris-OTT  289.187622
151               Adam Fox-NYR  287.205911
44        William Nylander-TOR  287.149689
28        Joel Eriksson Ek-MIN  286.502609
125       Alex Pietrangelo-VGK  285.465092
69          Filip Forsberg-NSH  285.216246
128           Ryan Hartman-MIN  285.154710
189          Robert Thomas-STL  285.139953
112         Miro Heiskanen-DAL  283.677012
183           Quinn Hughes-VAN  283.018483
38         Jason Robertson-DAL  282.580637
105           Dylan Larkin-DET  281.943542
83            Aaron Ekblad-FLA  281.044958
19          Nikolaj Ehlers-WPG  279.836902
154          Morgan Rielly-TOR  275.073315
50       Andrei Svechnikov-CAR  274.527122
130          Ivan Provorov-PHI  273.939010
18          Mark Scheifele-WPG  273.183522
132          Thomas Chabot-OTT  271.994826
106          Shea Theodore-VGK  271.769781
101        Mikael Backlund-CGY  271.718708
56     Chandler Stephenson-VGK  271.695286
42          Artemi Panarin-NYR  270.854777
159         Tyler Bertuzzi-DET  270.623900
216             Torey Krug-STL  269.954002
143            Nicolas Roy-VGK  269.782762
174     Vladimir Tarasenko-STL  269.563627
122           Justin Faulk-STL  269.006572
155       Teuvo Teravainen-CAR  268.015455
39         Drake Batherson-OTT  267.537044
153         Tanner Jeannot-NSH  267.357396
149          Rasmus Dahlin-BUF  265.758832
41             Jeff Carter-PIT  265.522263
142         Mattias Ekholm-NSH  264.467826
281           Morgan Frost-PHI  264.434953
119          Ryan Johansen-NSH  264.248840
206           Jacob Trouba-NYR  264.025997
30   Jonathan Marchessault-VGK  263.876610
89         Anthony Duclair-FLA  261.673899
99            Jonas Brodin-MIN  261.388785
168         Josh Morrissey-WPG  260.884685
202         Travis Sanheim-PHI  260.780823
62          Clayton Keller-ARI  260.460776
31        Carter Verhaeghe-FLA  260.178599
63            Jordan Kyrou-STL  257.363325
198          Jaccob Slavin-CAR  256.608898
197            Brady Skjei-CAR  255.783274
48     Ryan Nugent-Hopkins-EDM  254.805983
120           Jeff Skinner-BUF  254.626377
193             Neal Pionk-WPG  254.542742
111           Tyson Barrie-EDM  254.349117
60     Jean-Gabriel Pageau-NYI  253.809189
170            Adam Pelech-

In [12]:
three_year_pred = [yearly_player_data[i] for i in [9,10,11]]
three_year_pred = mx.merge_dataframes(three_year_pred, yearly_player_data[11])
three_year_pred.drop(columns=["Predicted_Fantasy_Points"], inplace=True)
three_year_df = mx.get_name_predictions(three_year_regr, three_year_pred)
three_year_df.sort_values(by="Prediction", ascending=False, inplace=True)
#pd.options.display.max_rows = 978
display(three_year_df)

Name  Prediction
1          Auston Matthews-TOR  351.749761
10        Patrice Bergeron-BOS  317.096773
6         Nathan MacKinnon-COL  305.963115
2           Leon Draisaitl-EDM  296.904605
41       Aleksander Barkov-FLA  295.263438
7           Connor McDavid-EDM  295.111459
48          Mikko Rantanen-COL  290.611996
36       Gabriel Landeskog-COL  287.442009
26       Andrei Svechnikov-CAR  280.405776
49             Roope Hintz-DAL  279.864844
12          Elias Lindholm-CGY  275.025394
0           David Pastrnak-BOS  274.453811
5            Sebastian Aho-CAR  274.167257
34           Brady Tkachuk-OTT  271.553210
21            John Tavares-TOR  264.658548
59           Sidney Crosby-PIT  258.867197
14           Brad Marchand-BOS  257.997443
3           Mika Zibanejad-NYR  257.609792
29               Bo Horvat-VAN  257.240649
17             J.T. Miller-VAN  256.608986
15        Elias Pettersson-VAN  256.565955
40           Jake Guentzel-PIT  256.470378
98            Ryan Hartman-MIN  248.562254
37          Filip Forsberg-NSH  244.211538
122          Thomas Chabot-OTT  244.034758
107       Joel Eriksson Ek-MIN  243.621110
52            Dylan Larkin-DET  242.075683
24          Nikolaj Ehlers-WPG  238.344778
204            Josh Norris-OTT  236.310617
11        William Nylander-TOR  236.275635
78       Valeri Nichushkin-COL  234.450393
71            Joe Pavelski-DAL  230.457694
25           Chris Kreider-NYR  229.215729
62            Brock Boeser-VAN  228.309860
83              Cale Makar-COL  227.049325
192          Tage Thompson-BUF  225.388351
13          Mark Scheifele-WPG  225.177035
27          Travis Konecny-PHI  224.230073
110         Miro Heiskanen-DAL  224.158203
30   Jonathan Marchessault-VGK  223.547747
16              Bryan Rust-PIT  223.075334
9           Artemi Panarin-NYR  221.314474
39          Tyler Bertuzzi-DET  220.709391
4              Kyle Connor-WPG  219.611626
76            Matt Duchene-NSH  218.066149
55       Andrew Mangiapane-CGY  217.316991
129            Nicolas Roy-VGK  216.800803
22           Evgeni Malkin-PIT  216.002656
33           Blake Wheeler-WPG  215.155371
31          Sean Couturier-PHI  215.148386
133           Aaron Ekblad-FLA  214.742433
57            Tyler Seguin-DAL  213.563216
94           Robert Thomas-STL  211.772021
47            Jake DeBrusk-BOS  211.171733
201        Jason Robertson-DAL  209.798310
127         Charlie McAvoy-BOS  209.119516
67        Teuvo Teravainen-CAR  207.044254
109               Adam Fox-NYR  205.992813
104           Jordan Staal-CAR  205.383959
134          Darnell Nurse-EDM  205.119406
68        William Karlsson-VGK  202.572613
154          Morgan Rielly-TOR  202.094998
66             Kris Letang-PIT  200.785756
113           Joel Farabee-PHI  200.668253
60              Roman Josi-NSH  200.268268
32     Ryan Nugent-Hopkins-EDM  200.169145
112           Quinn Hughes-VAN  199.427728
75           Ivan Provorov-PHI  199.285249
54          Clayton Keller-ARI  198.621213
90     Chandler Stephenson-VGK  198.496672
80           Ryan O'Reilly-STL  198.370238
126       Rasmus Andersson-CGY  198.334942
82          Jakob Chychrun-ARI  197.036483
20            Brock Nelson-NYI  194.853379
73            Jeff Skinner-BUF  194.462931
143          Rasmus Dahlin-BUF  192.882425
18            Reilly Smith-VGK  192.683208
77           Shea Theodore-VGK  192.660366
63            Martin Necas-CAR  192.176245
176            Noah Dobson-NYI  191.697102
72           Ryan Johansen-NSH  191.259900
42              Anders Lee-NYI  191.145635
149     Vladimir Tarasenko-STL  190.343555
116          Jaccob Slavin-CAR  188.691623
74            Filip Chytil-NYR  188.094749
56         Mikael Granlund-NSH  187.821914
46           Mathew Barzal-NYI  187.135650
123             Neal Pionk-WPG  186.848641
35              Mark Stone-VGK  185.667878
146          Samuel Girard-COL  185.225762
87           Nick Schmaltz-ARI  184.354637
19     Jean-Gabriel Pageau-NYI  184.112633
108         Pierre Engvall-

In [13]:
one_year_pred = yearly_player_data[11].copy()
one_year_pred.drop(columns=["Fantasy_Points"], inplace=True)
one_year_df = mx.get_name_predictions(one_year_RF, one_year_pred)
one_year_df.sort_values(by="Prediction", ascending=False, inplace=True)
#pd.options.display.max_rows = 978
display(one_year_df)

Name  Prediction
18          Connor McDavid-EDM    424.2775
48         Auston Matthews-TOR    409.9640
7        Aleksander Barkov-FLA    405.8320
83          David Pastrnak-BOS    405.3735
20       Gabriel Landeskog-COL    405.1580
37        Nathan MacKinnon-COL    404.8150
477         Mark Scheifele-WPG    400.6020
8           Mikko Rantanen-COL    397.0615
53           Sidney Crosby-PIT    394.8310
19         Kirill Kaprizov-MIN    391.6575
25        Patrice Bergeron-BOS    391.0895
82           Jake Guentzel-PIT    388.3760
132           Matt Duchene-NSH    387.2920
62          Leon Draisaitl-EDM    385.6260
66           Brad Marchand-BOS    383.5550
88          Filip Forsberg-NSH    381.4730
480           Dylan Larkin-DET    380.4255
96           Ryan O'Reilly-STL    376.5665
394            Josh Norris-OTT    376.0545
21             Sam Bennett-FLA    374.0225
154              Bo Horvat-VAN    371.3565
45         Mats Zuccarello-MIN    370.4710
358           Brock Nelson-NYI    370.3105
74             J.T. Miller-VAN    369.7135
405           John Tavares-TOR    368.9110
57          Nikolaj Ehlers-WPG    365.9980
67        Joel Eriksson Ek-MIN    363.5450
15          Mika Zibanejad-NYR    363.3685
124             Bryan Rust-PIT    363.0650
52           Chris Kreider-NYR    361.7040
467          Mathew Barzal-NYI    361.3960
466          Blake Wheeler-WPG    359.7470
28            Sam Reinhart-FLA    358.7390
55       Andrei Svechnikov-CAR    358.2405
44          Brayden Schenn-STL    357.5825
189       Elias Pettersson-VAN    357.2810
46          Artemi Panarin-NYR    356.6105
65         Jason Robertson-DAL    356.3235
156         Clayton Keller-ARI    355.6250
321            Kyle Connor-WPG    355.1405
501           Jared McCann-SEA    354.9835
56           Sebastian Aho-CAR    354.3440
155  Jonathan Marchessault-VGK    352.8110
2               Cale Makar-COL    352.3740
30            Evander Kane-EDM    351.1185
63           Robert Thomas-STL    350.9655
38        Teuvo Teravainen-CAR    350.6525
482           Patrick Kane-CHI    347.4715
43       Valeri Nichushkin-COL    347.4400
323              Alex Tuch-BUF    346.5130
418       William Nylander-TOR    346.2930
476          Tage Thompson-BUF    345.4825
440         Tyler Bertuzzi-DET    345.3825
0           Elias Lindholm-CGY    344.6950
433          Evgeni Malkin-PIT    344.2715
17        Pavel Buchnevich-STL    344.0055
373      Pierre-Luc Dubois-WPG    343.4775
359           Brock Boeser-VAN    341.8375
160    Ryan Nugent-Hopkins-EDM    338.4085
441             Anders Lee-NYI    336.5065
419             Zach Hyman-EDM    335.8845
295           Cam Atkinson-PHI    335.8745
13            Ryan Hartman-MIN    333.9570
148        Drake Batherson-OTT    333.5785
140    Chandler Stephenson-VGK    332.6060
395          Brady Tkachuk-OTT    332.5180
73             Roope Hintz-DAL    331.4750
123     Vladimir Tarasenko-STL    330.0535
6             Aaron Ekblad-FLA    329.6760
102           Jordan Kyrou-STL    329.0865
129             Mark Stone-VGK    327.8090
458           Jeff Skinner-BUF    327.5500
360          Tyler Toffoli-CGY    327.5030
490           Tyler Seguin-DAL    326.9610
39        Jesse Puljujarvi-EDM    326.3960
423        Mikael Granlund-NSH    326.3875
495           Robby Fabbri-DET    324.5665
84              Roman Josi-NSH    324.3895
54         Anthony Duclair-FLA    323.3965
294          Ryan Johansen-NSH    321.8575
503            Tim Stutzle-OTT    321.7095
94            Joe Pavelski-DAL    320.9530
222         Rickard Rakell-PIT    318.9250
406            Jeff Carter-PIT    318.5510
11           Anton Lundell-FLA    318.0045
1              Devon Toews-COL    317.5420
505          Jordan Eberle-SEA    317.4755
59                Adam Fox-NYR    316.1875
50             Kris Letang-PIT    315.0515
158       William Karlsson-VGK    314.3550
12          Jared Spurgeon-MIN    313.6055
190          Nick Schmaltz-ARI    313.3105
223    Jean-Gabriel Pageau-

In [14]:
two_year_pred = [yearly_player_data[i] for i in [10,11]]
two_year_pred = mx.merge_dataframes(two_year_pred, yearly_player_data[11])
two_year_pred.drop(columns=["Predicted_Fantasy_Points"], inplace=True)
two_year_df = mx.get_name_predictions(two_year_RF, two_year_pred)
two_year_df.sort_values(by="Prediction", ascending=False, inplace=True)
#pd.options.display.max_rows = 978
display(two_year_df)

Name  Prediction
15        Patrice Bergeron-BOS    413.9755
7        Aleksander Barkov-FLA    413.8980
16              Bryan Rust-PIT    404.6885
3           Mikko Rantanen-COL    403.9090
11          Mika Zibanejad-NYR    403.8420
0          Auston Matthews-TOR    396.1555
20          David Pastrnak-BOS    395.0655
9            Sidney Crosby-PIT    394.6250
21        Nathan MacKinnon-COL    392.8510
77         Mats Zuccarello-MIN    390.2750
69          Filip Forsberg-NSH    389.5670
22       Gabriel Landeskog-COL    388.8310
48     Ryan Nugent-Hopkins-EDM    388.7430
14           Jake Guentzel-PIT    384.9270
62          Clayton Keller-ARI    384.3980
4            Brad Marchand-BOS    383.0645
18          Mark Scheifele-WPG    381.4625
53           Blake Wheeler-WPG    380.8835
151               Adam Fox-NYR    380.1605
42          Artemi Panarin-NYR    379.4315
10           Ryan O'Reilly-STL    378.0040
138           Matt Duchene-NSH    377.1130
1           Connor McDavid-EDM    375.9345
27               Bo Horvat-VAN    375.6280
2           Leon Draisaitl-EDM    375.1405
12           Sebastian Aho-CAR    374.7805
8             Joe Pavelski-DAL    374.1090
47          Brayden Schenn-STL    372.5360
104            Devon Toews-COL    371.6520
110             Roman Josi-NSH    369.4905
37             Josh Norris-OTT    369.1740
84           Nick Schmaltz-ARI    368.5965
113             Cale Makar-COL    366.2655
106          Shea Theodore-VGK    365.8915
174     Vladimir Tarasenko-STL    365.0930
83            Aaron Ekblad-FLA    365.0450
52            Patrick Kane-CHI    364.4235
26          Elias Lindholm-CGY    364.4155
51             J.T. Miller-VAN    362.2765
123            Kris Letang-PIT    362.2030
28        Joel Eriksson Ek-MIN    361.9655
50       Andrei Svechnikov-CAR    361.4880
66         Mikael Granlund-NSH    360.9585
33            Brock Nelson-NYI    360.7025
43           Mathew Barzal-NYI    359.0045
23           Chris Kreider-NYR    358.3660
189          Robert Thomas-STL    358.2765
55             Roope Hintz-DAL    357.7995
38         Jason Robertson-DAL    357.5205
30   Jonathan Marchessault-VGK    357.5040
154          Morgan Rielly-TOR    357.2845
6              Kyle Connor-WPG    357.1145
25            John Tavares-TOR    356.1820
63            Jordan Kyrou-STL    355.3160
13            Brock Boeser-VAN    355.2415
19          Nikolaj Ehlers-WPG    354.5810
89         Anthony Duclair-FLA    351.7530
56     Chandler Stephenson-VGK    351.4630
36           Brady Tkachuk-OTT    351.2645
5          Kirill Kaprizov-MIN    350.6955
105           Dylan Larkin-DET    349.4065
88       Valeri Nichushkin-COL    349.3660
86             Sam Bennett-FLA    348.4425
44        William Nylander-TOR    346.4365
31        Carter Verhaeghe-FLA    344.1750
159         Tyler Bertuzzi-DET    343.9945
149          Rasmus Dahlin-BUF    343.7045
119          Ryan Johansen-NSH    343.0605
150         Charlie McAvoy-BOS    341.7435
93             Taylor Hall-BOS    340.6255
95        Elias Pettersson-VAN    339.1335
34       Andrew Mangiapane-CGY    337.0050
160       Rasmus Andersson-CGY    336.6330
155       Teuvo Teravainen-CAR    336.5125
120           Jeff Skinner-BUF    336.0345
183           Quinn Hughes-VAN    335.9495
73             Tim Stutzle-OTT    331.5115
98       Pierre-Luc Dubois-WPG    329.3480
128           Ryan Hartman-MIN    326.4810
167           Noah Hanifin-CGY    325.9975
81          Travis Konecny-PHI    324.4230
184            Noah Dobson-NYI    323.9250
114          Tage Thompson-BUF    320.5765
122           Justin Faulk-STL    318.8355
57            Reilly Smith-VGK    317.3165
67         Victor Olofsson-BUF    316.5250
70              Anders Lee-NYI    316.1155
214           Tyler Seguin-DAL    314.5320
164         Ivan Barbashev-STL    313.7785
24            Joel Farabee-PHI    313.5365
39         Drake Batherson-OTT    309.3070
79              Jamie Benn-DAL    308.1730
17              Mark Stone-

In [15]:
three_year_pred = [yearly_player_data[i] for i in [9,10,11]]
three_year_pred = mx.merge_dataframes(three_year_pred, yearly_player_data[11])
three_year_pred.drop(columns=["Predicted_Fantasy_Points"], inplace=True)
three_year_df = mx.get_name_predictions(three_year_RF, three_year_pred)
three_year_df.sort_values(by="Prediction", ascending=False, inplace=True)
#pd.options.display.max_rows = 978
display(three_year_df)

Name  Prediction
0           David Pastrnak-BOS    395.0360
10        Patrice Bergeron-BOS    392.3680
14           Brad Marchand-BOS    391.7775
36       Gabriel Landeskog-COL    389.9310
1          Auston Matthews-TOR    378.0025
6         Nathan MacKinnon-COL    377.3730
41       Aleksander Barkov-FLA    376.8630
48          Mikko Rantanen-COL    369.2140
7           Connor McDavid-EDM    366.3115
9           Artemi Panarin-NYR    361.4340
11        William Nylander-TOR    359.7785
21            John Tavares-TOR    357.2025
13          Mark Scheifele-WPG    356.5755
16              Bryan Rust-PIT    356.2225
40           Jake Guentzel-PIT    356.1010
37          Filip Forsberg-NSH    352.9615
59           Sidney Crosby-PIT    350.7855
8             Patrick Kane-CHI    350.1920
24          Nikolaj Ehlers-WPG    348.8590
71            Joe Pavelski-DAL    348.3320
5            Sebastian Aho-CAR    348.1240
4              Kyle Connor-WPG    346.9230
83              Cale Makar-COL    345.5355
26       Andrei Svechnikov-CAR    345.1565
46           Mathew Barzal-NYI    343.1445
32     Ryan Nugent-Hopkins-EDM    342.5165
2           Leon Draisaitl-EDM    341.2760
22           Evgeni Malkin-PIT    340.5175
30   Jonathan Marchessault-VGK    340.1915
87           Nick Schmaltz-ARI    339.3505
34           Brady Tkachuk-OTT    338.7775
62            Brock Boeser-VAN    334.5915
35              Mark Stone-VGK    334.0750
3           Mika Zibanejad-NYR    333.1065
76            Matt Duchene-NSH    331.8520
23          Brayden Schenn-STL    330.9925
65         Mats Zuccarello-MIN    330.1565
80           Ryan O'Reilly-STL    330.0950
29               Bo Horvat-VAN    330.0140
17             J.T. Miller-VAN    329.3340
52            Dylan Larkin-DET    329.0885
49             Roope Hintz-DAL    328.6580
25           Chris Kreider-NYR    327.7720
12          Elias Lindholm-CGY    327.5815
201        Jason Robertson-DAL    326.6695
60              Roman Josi-NSH    325.7000
54          Clayton Keller-ARI    324.0450
18            Reilly Smith-VGK    322.1220
33           Blake Wheeler-WPG    321.8440
67        Teuvo Teravainen-CAR    319.5685
66             Kris Letang-PIT    319.4960
15        Elias Pettersson-VAN    319.4310
68        William Karlsson-VGK    317.0170
39          Tyler Bertuzzi-DET    314.9185
94           Robert Thomas-STL    313.9120
109               Adam Fox-NYR    313.0645
27          Travis Konecny-PHI    312.6000
77           Shea Theodore-VGK    312.3385
20            Brock Nelson-NYI    311.2800
57            Tyler Seguin-DAL    308.5805
78       Valeri Nichushkin-COL    308.2185
72           Ryan Johansen-NSH    307.6375
50      James van Riemsdyk-PHI    307.0570
42              Anders Lee-NYI    306.1080
31          Sean Couturier-PHI    305.1135
112           Quinn Hughes-VAN    304.7310
204            Josh Norris-OTT    304.6780
55       Andrew Mangiapane-CGY    304.0280
133           Aaron Ekblad-FLA    303.6935
148        Drake Batherson-OTT    303.6765
45         Victor Olofsson-BUF    299.8255
90     Chandler Stephenson-VGK    299.7875
51              Jamie Benn-DAL    296.2310
127         Charlie McAvoy-BOS    292.8780
154          Morgan Rielly-TOR    292.7945
107       Joel Eriksson Ek-MIN    290.1680
147           Jordan Kyrou-STL    290.1550
122          Thomas Chabot-OTT    284.1135
98            Ryan Hartman-MIN    283.9795
73            Jeff Skinner-BUF    283.7220
192          Tage Thompson-BUF    283.7195
63            Martin Necas-CAR    283.6215
104           Jordan Staal-CAR    283.2955
58         Mikael Backlund-CGY    281.3420
116          Jaccob Slavin-CAR    279.8645
70             Josh Bailey-NYI    278.1300
143          Rasmus Dahlin-BUF    277.0625
61           Charlie Coyle-BOS    277.0185
56         Mikael Granlund-NSH    276.8275
28             Kevin Hayes-PHI    276.2855
149     Vladimir Tarasenko-STL    275.3160
81          Jared Spurgeon-MIN    274.2570
86          Ivan Barbashev-

Section 6: Conclusion and Next Steps

The predictions made by all of these models make sense; all of the predicted top players are still some of the top players in the league this year, and many of the predictions match up with predictions made by ESPN. One step that could be done is aggregating the six models together to get an average points prediction, and listing the players that way. Another thing that can be done to improve the models is incorporate injury data; there are some elite players that were injured in some part of the past three years, and their predictions are more pessemistic than other players. Another improvement could be to try and scale for the COVID-shortened 2019-2020 and 2020-2021 seasons. There were many logistical issues that contributed to fewer games and lower scoring in those years, and a scaling of goal/assist values could be beneficial to the models.

Overall, I'm happy with how the models performed. After the 2022-2023 regular season, I will see how well they were able to predict some of the outliers, and I'll use that new data to make a prediction for the 2023-2024 season.

ACKNOWLEDGEMENTS:

Thank you to Rotowire and Moneypuck for making your NHL data easy for someone like me to utilize in a project like this, and thank you to Peter Tanner of Moneypuck not just for creating such a valuable resource, but for being responsive to questions I was having about your dataset.